In [ ]:
#!pip3 install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118

In [1]:
import torch

# GPU varsa kullan, yoksa CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)


A module that was compiled using NumPy 1.x cannot be run in
NumPy 2.0.2 as it may crash. To support both 1.x and 2.x
versions of NumPy, modules must be compiled with NumPy 2.0.
Some module may need to rebuild instead e.g. with 'pybind11>=2.12'.

If you are a user of the module, the easiest solution will be to
downgrade to 'numpy<2' or try to upgrade the affected module.
We expect that some modules will need time to support NumPy 2.

Traceback (most recent call last):  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  File "/usr/local/lib/python3.11/dist-packages/colab_kernel_launcher.py", line 37, in <module>
    ColabKernelApp.launch_instance()
  File "/usr/local/lib/python3.11/dist-packages/traitlets/config/application.py", line 992, in launch_instance
    app.start()
  File "/usr/local/lib/python3.11/dist-packages/ipykernel/kernelapp.py", line 712, in start
    self.io_loop.start()
  File "/usr/local/lib/python3.11/dist-package

Using device: cuda


In [53]:
#!nvidia-smi

Fri Jul 25 10:36:41 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA L4                      Off |   00000000:00:03.0 Off |                    0 |
| N/A   64C    P0             32W /   72W |    6489MiB /  23034MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [4]:
#!pip uninstall -y torchtext
#!pip install torchtext==0.17.0
#!pip uninstall -y transformers
#!pip install transformers==4.31.0  # or another 4.x release that includes the sequence‐classification classes

  Using cached torchtext-0.17.0-cp311-cp311-manylinux1_x86_64.whl.metadata (7.6 kB)
  Using cached torch-2.2.0-cp311-cp311-manylinux1_x86_64.whl.metadata (25 kB)
  Using cached torchdata-0.7.1-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (13 kB)
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_6

Found existing installation: transformers 4.31.0
Uninstalling transformers-4.31.0:
  Successfully uninstalled transformers-4.31.0
  Using cached transformers-4.31.0-py3-none-any.whl.metadata (116 kB)
Using cached transformers-4.31.0-py3-none-any.whl (7.4 MB)
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
sentence-transformers 4.1.0 requires transformers<5.0.0,>=4.41.0, but you have transformers 4.31.0 which is incompatible.


In [2]:
import os
import re
import pandas as pd

import torch

from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence

from torchtext.vocab import build_vocab_from_iterator

In [24]:
# Veri dosyanızın yolunu belirtin
file_path = 'main_dataset.csv' # Burayı kendi dosya yolunuzla değiştirin

# Veriyi pandas DataFrame'ine yükleyin
try:
    df = pd.read_csv(file_path)
    print("Veri başarıyla yüklendi.")
    print("DataFrame'in ilk 5 satırı:")
    display(df.head())
except FileNotFoundError:
    print(f"Hata: '{file_path}' dosyası bulunamadı. Lütfen dosya yolunu kontrol edin.")
except Exception as e:
    print(f"Veri yüklenirken bir hata oluştu: {e}")

Veri başarıyla yüklendi.
DataFrame'in ilk 5 satırı:


2401  Borderlands  Positive  \
0  2401  Borderlands  Positive   
1  2401  Borderlands  Positive   
2  2401  Borderlands  Positive   
3  2401  Borderlands  Positive   
4  2401  Borderlands  Positive   

  im getting on borderlands and i will murder you all ,  
0  I am coming to the borders and I will kill you...     
1  im getting on borderlands and i will kill you ...     
2  im coming on borderlands and i will murder you...     
3  im getting on borderlands 2 and i will murder ...     
4  im getting into borderlands and i can murder y...

In [25]:
new_columns = ['index', 'entity', 'sentiment', 'tweet']
df.columns = new_columns

In [26]:
df

index       entity sentiment  \
0       2401  Borderlands  Positive   
1       2401  Borderlands  Positive   
2       2401  Borderlands  Positive   
3       2401  Borderlands  Positive   
4       2401  Borderlands  Positive   
...      ...          ...       ...   
74676   9200       Nvidia  Positive   
74677   9200       Nvidia  Positive   
74678   9200       Nvidia  Positive   
74679   9200       Nvidia  Positive   
74680   9200       Nvidia  Positive   

                                                   tweet  
0      I am coming to the borders and I will kill you...  
1      im getting on borderlands and i will kill you ...  
2      im coming on borderlands and i will murder you...  
3      im getting on borderlands 2 and i will murder ...  
4      im getting into borderlands and i can murder y...  
...                                                  ...  
74676  Just realized that the Windows partition of my...  
74677  Just realized that my Mac window partition is ...  
74678  Just realized the windows partition of my Mac ...  
74679  Just realized between the windows partition of...  
74680  Just like the windows partition of my Mac is l...  

[74681 rows x 4 columns]

In [27]:
df = df.dropna(subset=['tweet','entity']).reset_index(drop=True)

In [28]:
from collections import Counter
import torch

# 1) Tokenizer fonksiyonu (öncekiyle aynı)
def clean_text(text: str) -> str:
    text = text.lower()
    text = re.sub(r'http\S+|@\w+|#\w+', '', text)
    text = re.sub(r'[^\w\s\[\]]', '', text)
    return text.strip()

def mark_entity(text: str, entity: str) -> str:
    return text.replace(entity, f"[E_START] {entity} [E_END]")

def tokenize(text: str):
    return clean_text(text).split()

# 2) Tüm token’ları say
counter = Counter()
for _, row in df.iterrows():
    marked = mark_entity(row['tweet'], row['entity'])
    counter.update(tokenize(marked))
    counter.update(tokenize(row['entity']))

# 3) Vocab listesi ve sözlükler
vocab_list = ["<pad>", "<unk>"] + [tok for tok, freq in counter.items() if freq >= 1]
stoi = {tok: idx for idx, tok in enumerate(vocab_list)}
itos = {idx: tok for tok, idx in stoi.items()}

# 4) Yardımcı dönüşüm fonksiyonu
def tokens_to_indices(tokens):
    return [stoi.get(tok, stoi["<unk>"]) for tok in tokens]

# 5) VOCAB_SIZE’ı tanımla
VOCAB_SIZE = len(stoi)
print(f"Vocabulary size: {VOCAB_SIZE}")


Vocabulary size: 40124


In [29]:
import numpy as np
import torch

# 2.1 Parametreler
EMBED_DIM = 200
VOCAB_SIZE = len(stoi)

# 2.2 GloVe sözlüğünü oluştur (düzgün yol)
emb_index = {}
with open('glove.twitter.27B.200d.txt', 'r', encoding='utf8') as f:
    for line in f:
        vals = line.split()
        word = vals[0]
        vec = np.asarray(vals[1:], dtype='float32')
        emb_index[word] = vec

# 2.3 Ağırlık matrisini başlat ve doldur
weight_matrix = np.zeros((VOCAB_SIZE, EMBED_DIM), dtype='float32')
for token, idx in stoi.items():
    if token in emb_index:
        weight_matrix[idx] = emb_index[token]
    else:
        weight_matrix[idx] = np.random.normal(scale=0.6, size=(EMBED_DIM,))

# 2.4 Torch tensor’a çevirirken dtype belirt
embedding_weights = torch.tensor(weight_matrix, dtype=torch.float32)

# Kontrol
print("Embedding ağırlıkları shape:", embedding_weights.shape)
print("Dtype:", embedding_weights.dtype)


ValueError: could not convert string to float: '-'

In [31]:
print("Unique sentiment labels:", df['sentiment'].unique())
print(df['sentiment'].value_counts())


Unique sentiment labels: ['Positive' 'Neutral' 'Negative' 'Irrelevant']
sentiment
Negative      22358
Positive      20654
Neutral       18108
Irrelevant    12875
Name: count, dtype: int64


In [32]:
# 1) Benzersiz sınıfları al
unique_labels = list(df['sentiment'].unique())
print("Found labels:", unique_labels)

# 2) Label → index mapping
label_map = {label: idx for idx, label in enumerate(unique_labels)}
print("label_map:", label_map)

# 3) Kaç sınıf var?
num_classes = len(unique_labels)
print("Number of classes:", num_classes)

# 4) Yeni numeric label sütunu oluştur
df['label_idx'] = df['sentiment'].map(label_map)


Found labels: ['Positive', 'Neutral', 'Negative', 'Irrelevant']
label_map: {'Positive': 0, 'Neutral': 1, 'Negative': 2, 'Irrelevant': 3}
Number of classes: 4


In [33]:
import pandas as pd
import re
import torch
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence

# ——— 1) Temizleme ve işaretleme fonksiyonları ———
def clean_text(text: str) -> str:
    text = text.lower()
    text = re.sub(r'http\S+|@\w+|#\w+', '', text)
    text = re.sub(r'[^\w\s\[\]]', '', text)
    return text.strip()

def mark_entity(text, entity):
    text = "" if pd.isna(text) else str(text)
    entity = "" if pd.isna(entity) else str(entity)
    return text.replace(entity, f"[E_START] {entity} [E_END]")

def tokenize(text: str):
    return clean_text(text).split()





# ——— 3) Collate fonksiyonu ———
def collate_batch(batch):
    texts, ents, labels = zip(*batch)
    texts_padded = pad_sequence(texts, batch_first=True, padding_value=stoi["<pad>"])
    ents_padded  = pad_sequence(ents,  batch_first=True, padding_value=stoi["<pad>"])
    return texts_padded, ents_padded, torch.stack(labels)
from torch.utils.data import Dataset, DataLoader, random_split
import torch

# 5) Dataset sınıfını label_idx kullanacak şekilde güncelleyelim
class SentimentDataset(Dataset):
    def __init__(self, df, stoi):
        self.df = df.reset_index(drop=True)
        self.stoi = stoi

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        marked = mark_entity(row['tweet'], row['entity'])
        tweet_idxs = [self.stoi.get(tok, self.stoi["<unk>"]) for tok in tokenize(marked)]
        ent_idxs   = [self.stoi.get(tok, self.stoi["<unk>"]) for tok in tokenize(str(row['entity']))]
        label      = int(row['label_idx'])

        return (
            torch.tensor(tweet_idxs, dtype=torch.long),
            torch.tensor(ent_idxs,   dtype=torch.long),
            torch.tensor(label,      dtype=torch.long)
        )

# 6) Train/Val split ve DataLoader’lar
df = df.dropna(subset=['tweet','entity','sentiment','label_idx']).reset_index(drop=True)
train_size = int(0.8 * len(df))
val_size   = len(df) - train_size
train_df, val_df = random_split(df, [train_size, val_size], generator=torch.Generator().manual_seed(42))

train_ds = SentimentDataset(train_df.dataset.iloc[train_df.indices], stoi)
val_ds   = SentimentDataset(val_df.dataset.iloc[val_df.indices],   stoi)

BATCH_SIZE = 32
train_loader = DataLoader(train_ds, batch_size=BATCH_SIZE, shuffle=True,  collate_fn=collate_batch, pin_memory=True)
val_loader   = DataLoader(val_ds,   batch_size=BATCH_SIZE, shuffle=False, collate_fn=collate_batch, pin_memory=True)

print("DataLoader’lar hazır:", len(train_loader), "train batches,", len(val_loader), "val batches")


DataLoader’lar hazır: 1850 train batches, 463 val batches


In [34]:
# Eğitiminize başlamadan önce:
unique_labels = sorted(df['label_idx'].unique().tolist())
print("Label idx’ler:", unique_labels)
print("Num classes:", len(unique_labels))


Label idx’ler: [0, 1, 2, 3]
Num classes: 4


In [37]:
import torch
from torch.utils.data import random_split, DataLoader

# ——— 1) label_idx, SentimentDataset ve collate_batch hâlâ tanımlı varsayılıyor ———
# Eğer tanımlı değilse, lütfen önce önceki tanımları (mark_entity, tokenize, stoi, SentimentDataset, collate_batch) tekrar çalıştırın.

# ——— 2) Train/Val split ———
df = df.dropna(subset=['tweet','entity','sentiment','label_idx']).reset_index(drop=True)
train_size = int(0.8 * len(df))
val_size   = len(df) - train_size
train_df, val_df = random_split(df, [train_size, val_size], generator=torch.Generator().manual_seed(42))

# ——— 3) Dataset’leri oluştur ———
train_dataset = SentimentDataset(train_df.dataset.iloc[train_df.indices].reset_index(drop=True), stoi)
val_dataset   = SentimentDataset(  val_df.dataset.iloc[  val_df.indices].reset_index(drop=True), stoi)

# ——— 4) DataLoader’ları oluştur ———
BATCH_SIZE = 32
train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True,  collate_fn=collate_batch, pin_memory=True)
val_loader   = DataLoader(  val_dataset,   batch_size=BATCH_SIZE, shuffle=False, collate_fn=collate_batch, pin_memory=True)

print(f"✔ train_loader: {len(train_loader)} batch, val_loader: {len(val_loader)} batch")

# ——— 5) Tek bir örnekle smoke‑test (CPU’da) ———
device = torch.device("cpu")
sample_text, sample_ent, sample_label = train_dataset[0]
print("Sample label:", sample_label)
with torch.no_grad():
    out = model(sample_text.unsqueeze(0).to(device), sample_ent.unsqueeze(0).to(device))
print("Smoke‑test output shape:", out.shape)  # ([1, num_classes]) olması gerekir


✔ train_loader: 1850 batch, val_loader: 463 batch
Sample label: tensor(0)


RuntimeError: Expected all tensors to be on the same device, but found at least two devices, cuda:0 and cpu! (when checking argument for argument index in method wrapper_CUDA__index_select)

In [ ]:
import torch
import torch.nn as nn
from sklearn.metrics import accuracy_score

# 1) Device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# 2) Model
model = LSTMEntityModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    hidden_size=128,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)

# 3) Loss, Optimizer, Scheduler
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode="max", factor=0.5, patience=2, verbose=True
)

# 4) Training & Validation Loop
num_epochs = 10
best_val_acc = 0.0

for epoch in range(1, num_epochs+1):
    # — TRAIN —
    model.train()
    train_loss = 0.0
    for texts, ents, labels in train_loader:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)

        optimizer.zero_grad()
        logits = model(texts, ents)               # [B, num_classes]
        loss = criterion(logits, labels)
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        optimizer.step()

        train_loss += loss.item() * texts.size(0)

    avg_train_loss = train_loss / len(train_loader.dataset)

    # — VALIDATION —
    model.eval()
    all_preds, all_labels = [], []
    val_loss = 0.0
    with torch.no_grad():
        for texts, ents, labels in val_loader:
            texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
            logits = model(texts, ents)
            loss = criterion(logits, labels)
            val_loss += loss.item() * texts.size(0)

            all_preds.extend(logits.argmax(dim=1).cpu().tolist())
            all_labels.extend(labels.cpu().tolist())

    avg_val_loss = val_loss / len(val_loader.dataset)
    val_acc = accuracy_score(all_labels, all_preds)

    # — LR Scheduler & Checkpoint —
    scheduler.step(val_acc)
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        torch.save(model.state_dict(), "best_lstm_entity_model.pt")

    # — Epoch Özeti —
    print(f"Epoch {epoch:02d} | "
          f"Train Loss: {avg_train_loss:.4f} | "
          f"Val Loss: {avg_val_loss:.4f} | "
          f"Val Acc: {val_acc:.4f}")

print(f"\n🎉 Best Validation Accuracy: {best_val_acc:.4f}")
print("Model weights saved to best_lstm_entity_model.pt")


Using device: cuda


/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "


Epoch 01 | Train Loss: 1.0316 | Val Loss: 0.9217 | Val Acc: 0.6192
Epoch 02 | Train Loss: 0.8469 | Val Loss: 0.7765 | Val Acc: 0.6938
Epoch 03 | Train Loss: 0.6672 | Val Loss: 0.6685 | Val Acc: 0.7411
Epoch 04 | Train Loss: 0.4949 | Val Loss: 0.5905 | Val Acc: 0.7845
Epoch 05 | Train Loss: 0.3584 | Val Loss: 0.5474 | Val Acc: 0.8165
Epoch 06 | Train Loss: 0.2666 | Val Loss: 0.5677 | Val Acc: 0.8324
Epoch 07 | Train Loss: 0.2076 | Val Loss: 0.5926 | Val Acc: 0.8432
Epoch 08 | Train Loss: 0.1717 | Val Loss: 0.6875 | Val Acc: 0.8407
Epoch 09 | Train Loss: 0.1474 | Val Loss: 0.7031 | Val Acc: 0.8489
Epoch 10 | Train Loss: 0.1363 | Val Loss: 0.7775 | Val Acc: 0.8478

🎉 Best Validation Accuracy: 0.8489
Model weights saved to best_lstm_entity_model.pt


In [ ]:
import torch
import torch.nn as nn
from sklearn.metrics import accuracy_score

# Model
class GRUEntityModel(nn.Module):
    def __init__(self, vocab_size, embed_dim, hidden_size, num_classes, embedding_weights):
        super().__init__()
        self.embedding = nn.Embedding.from_pretrained(
            embedding_weights, freeze=True, padding_idx=stoi["<pad>"]
        )
        self.gru = nn.GRU(embed_dim, hidden_size, batch_first=True, bidirectional=True)
        self.fc  = nn.Sequential(
            nn.Linear(2*hidden_size + embed_dim, hidden_size),
            nn.ReLU(), nn.Dropout(0.5),
            nn.Linear(hidden_size, num_classes)
        )

    def forward(self, text, ent):
        emb = self.embedding(text)
        _, h_n = self.gru(emb)                    # h_n: [2,B,H]
        txt = torch.cat([h_n[0], h_n[1]], dim=1)  # [B,2H]
        ent_repr = self.embedding(ent).mean(1)    # [B,D]
        return self.fc(torch.cat([txt, ent_repr], dim=1))

# Kurulum
model = GRUEntityModel(len(stoi), EMBED_DIM, 128, num_classes, embedding_weights).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode="max", factor=0.5, patience=2)

# Eğitim/Validasyon
best_acc = 0.0
for epoch in range(1, 11):
    # Train
    model.train()
    tloss = 0
    for t,e,l in train_loader:
        t,e,l = t.to(device), e.to(device), l.to(device)
        optimizer.zero_grad()
        out = model(t,e)
        loss = criterion(out,l)
        loss.backward()
        optimizer.step()
        tloss += loss.item()*t.size(0)
    avg_t = tloss/len(train_loader.dataset)

    # Val
    model.eval()
    preds, trues, vloss = [], [], 0
    with torch.no_grad():
        for t,e,l in val_loader:
            t,e,l = t.to(device), e.to(device), l.to(device)
            out = model(t,e)
            vloss += criterion(out,l).item()*t.size(0)
            preds += out.argmax(1).cpu().tolist()
            trues += l.cpu().tolist()
    avg_v = vloss/len(val_loader.dataset)
    acc = accuracy_score(trues,preds)

    scheduler.step(acc)
    if acc>best_acc:
        best_acc=acc
        torch.save(model.state_dict(),"best_gru_entity_model.pt")

    print(f"[GRU] Epoch {epoch:02d} | Train Loss: {avg_t:.4f} | Val Loss: {avg_v:.4f} | Val Acc: {acc:.4f}")

print(f"🎯 Best GRU Val Acc: {best_acc:.4f}")


[GRU] Epoch 01 | Train Loss: 1.0139 | Val Loss: 0.8901 | Val Acc: 0.6309
[GRU] Epoch 02 | Train Loss: 0.8053 | Val Loss: 0.7309 | Val Acc: 0.7070
[GRU] Epoch 03 | Train Loss: 0.5775 | Val Loss: 0.5932 | Val Acc: 0.7744
[GRU] Epoch 04 | Train Loss: 0.3786 | Val Loss: 0.5312 | Val Acc: 0.8159
[GRU] Epoch 05 | Train Loss: 0.2623 | Val Loss: 0.5535 | Val Acc: 0.8284
[GRU] Epoch 06 | Train Loss: 0.2018 | Val Loss: 0.5581 | Val Acc: 0.8374
[GRU] Epoch 07 | Train Loss: 0.1679 | Val Loss: 0.5977 | Val Acc: 0.8433
[GRU] Epoch 08 | Train Loss: 0.1463 | Val Loss: 0.6216 | Val Acc: 0.8480
[GRU] Epoch 09 | Train Loss: 0.1362 | Val Loss: 0.6494 | Val Acc: 0.8449
[GRU] Epoch 10 | Train Loss: 0.1267 | Val Loss: 0.6165 | Val Acc: 0.8572
🎯 Best GRU Val Acc: 0.8572


In [ ]:
import torch.nn as nn

# Model
class CNNLSTMEntityModel(nn.Module):
    def __init__(self, vocab_size, embed_dim, num_filters, filter_size, hidden_size, num_classes, embedding_weights):
        super().__init__()
        self.embedding = nn.Embedding.from_pretrained(
            embedding_weights, freeze=True, padding_idx=stoi["<pad>"]
        )
        self.conv = nn.Conv1d(embed_dim, num_filters, kernel_size=filter_size, padding=filter_size//2)
        self.lstm = nn.LSTM(num_filters, hidden_size, batch_first=True, bidirectional=True)
        self.fc   = nn.Sequential(
            nn.Linear(2*hidden_size + embed_dim, hidden_size),
            nn.ReLU(), nn.Dropout(0.5),
            nn.Linear(hidden_size, num_classes)
        )

    def forward(self, text, ent):
        emb = self.embedding(text).transpose(1,2)    # [B,D,T]
        conv = self.conv(emb).transpose(1,2)         # [B,T,F]
        _, (h_n, _) = self.lstm(conv)
        txt = torch.cat([h_n[0], h_n[1]], dim=1)
        ent_repr = self.embedding(ent).mean(1)
        return self.fc(torch.cat([txt, ent_repr], dim=1))

# Kurulum
model = CNNLSTMEntityModel(
    len(stoi), EMBED_DIM, num_filters=100, filter_size=3,
    hidden_size=128, num_classes=num_classes, embedding_weights=embedding_weights
).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode="max", factor=0.5, patience=2)

# Eğitim döngüsü (LSTM ile aynı şablon)
best_acc = 0.0
for epoch in range(1,11):
    # Train
    model.train(); tloss=0
    for t,e,l in train_loader:
        t,e,l = t.to(device), e.to(device), l.to(device)
        optimizer.zero_grad()
        out = model(t,e)
        loss = criterion(out,l)
        loss.backward(); optimizer.step()
        tloss += loss.item()*t.size(0)
    avg_t = tloss/len(train_loader.dataset)

    # Val
    model.eval(); preds, trues, vloss = [],[],0
    with torch.no_grad():
        for t,e,l in val_loader:
            t,e,l = t.to(device), e.to(device), l.to(device)
            out = model(t,e)
            vloss += criterion(out,l).item()*t.size(0)
            preds += out.argmax(1).cpu().tolist()
            trues += l.cpu().tolist()
    avg_v = vloss/len(val_loader.dataset)
    acc = accuracy_score(trues,preds)

    scheduler.step(acc)
    if acc>best_acc:
        best_acc=acc
        torch.save(model.state_dict(),"best_cnnlstm_entity_model.pt")

    print(f"[CNN+LSTM] Epoch {epoch:02d} | Train Loss: {avg_t:.4f} | Val Acc: {acc:.4f}")

print(f"🎯 Best CNN+LSTM Val Acc: {best_acc:.4f}")


[CNN+LSTM] Epoch 01 | Train Loss: 1.0554 | Val Acc: 0.6033
[CNN+LSTM] Epoch 02 | Train Loss: 0.9165 | Val Acc: 0.6439
[CNN+LSTM] Epoch 03 | Train Loss: 0.8092 | Val Acc: 0.6807
[CNN+LSTM] Epoch 04 | Train Loss: 0.6939 | Val Acc: 0.7120
[CNN+LSTM] Epoch 05 | Train Loss: 0.5821 | Val Acc: 0.7391
[CNN+LSTM] Epoch 06 | Train Loss: 0.4868 | Val Acc: 0.7582
[CNN+LSTM] Epoch 07 | Train Loss: 0.4104 | Val Acc: 0.7707
[CNN+LSTM] Epoch 08 | Train Loss: 0.3557 | Val Acc: 0.7783
[CNN+LSTM] Epoch 09 | Train Loss: 0.3135 | Val Acc: 0.7854
[CNN+LSTM] Epoch 10 | Train Loss: 0.2841 | Val Acc: 0.7844
🎯 Best CNN+LSTM Val Acc: 0.7854


In [ ]:
import torch.nn as nn

# Model
class CNNTextModel(nn.Module):
    def __init__(self, vocab_size, embed_dim, num_filters, filter_sizes, hidden_size, num_classes, embedding_weights):
        super().__init__()
        self.embedding = nn.Embedding.from_pretrained(
            embedding_weights, freeze=True, padding_idx=stoi["<pad>"]
        )
        self.convs = nn.ModuleList([
            nn.Conv1d(embed_dim, num_filters, fs, padding=fs//2) for fs in filter_sizes
        ])
        self.fc = nn.Sequential(
            nn.Linear(len(filter_sizes)*num_filters, hidden_size),
            nn.ReLU(), nn.Dropout(0.5),
            nn.Linear(hidden_size, num_classes)
        )

    def forward(self, text, _ent=None):
        emb = self.embedding(text).transpose(1,2)   # [B,D,T]
        convs = [torch.relu(conv(emb)).max(dim=2)[0] for conv in self.convs]  # list of [B,F]
        feat = torch.cat(convs, dim=1)               # [B,F*|sizes|]
        return self.fc(feat)                         # [B,C]

# Kurulum
model = CNNTextModel(
    len(stoi), EMBED_DIM, num_filters=100,
    filter_sizes=[3,4,5], hidden_size=128,
    num_classes=num_classes, embedding_weights=embedding_weights
).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode="max", factor=0.5, patience=2)

# Eğitim döngüsü
best_acc=0.0
for epoch in range(1,11):
    # Train
    model.train(); tloss=0
    for t,_,l in train_loader:  # ent’i kullanmıyoruz
        t,l = t.to(device), l.to(device)
        optimizer.zero_grad()
        out = model(t)
        loss=criterion(out,l)
        loss.backward(); optimizer.step()
        tloss += loss.item()*t.size(0)
    avg_t=tloss/len(train_loader.dataset)

    # Val
    model.eval(); preds,trues,vloss=[],[],0
    with torch.no_grad():
        for t,_,l in val_loader:
            t,l = t.to(device), l.to(device)
            out = model(t)
            vloss+=criterion(out,l).item()*t.size(0)
            preds += out.argmax(1).cpu().tolist()
            trues  += l.cpu().tolist()
    avg_v=vloss/len(val_loader.dataset)
    acc=accuracy_score(trues,preds)

    scheduler.step(acc)
    if acc>best_acc:
        best_acc=acc
        torch.save(model.state_dict(),"best_cnn_text_model.pt")

    print(f"[CNN] Epoch {epoch:02d} | Train Loss: {avg_t:.4f} | Val Acc: {acc:.4f}")

print(f"🎯 Best CNN Val Acc: {best_acc:.4f}")


[CNN] Epoch 01 | Train Loss: 1.0395 | Val Acc: 0.6524
[CNN] Epoch 02 | Train Loss: 0.6926 | Val Acc: 0.7431
[CNN] Epoch 03 | Train Loss: 0.4328 | Val Acc: 0.7830
[CNN] Epoch 04 | Train Loss: 0.3088 | Val Acc: 0.7945
[CNN] Epoch 05 | Train Loss: 0.2481 | Val Acc: 0.7992
[CNN] Epoch 06 | Train Loss: 0.2136 | Val Acc: 0.8076
[CNN] Epoch 07 | Train Loss: 0.1941 | Val Acc: 0.8065
[CNN] Epoch 08 | Train Loss: 0.1768 | Val Acc: 0.8112
[CNN] Epoch 09 | Train Loss: 0.1590 | Val Acc: 0.7986
[CNN] Epoch 10 | Train Loss: 0.1506 | Val Acc: 0.8061
🎯 Best CNN Val Acc: 0.8112


In [ ]:
#!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 395.9/395.9 kB 12.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 247.0/247.0 kB 18.1 MB/s eta 0:00:00


In [ ]:
import optuna
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score
from tqdm.auto import tqdm

def objective_lstm(trial):
    # Search space
    hidden_size  = trial.suggest_categorical("hidden_size", [64, 128, 256])
    dropout_rate = trial.suggest_float("dropout_rate", 0.2, 0.6)
    lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)
    batch_size   = trial.suggest_categorical("batch_size", [16, 32, 64])

    # DataLoaders
    tl = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, collate_fn=collate_batch)
    vl = DataLoader(val_dataset,   batch_size=batch_size, shuffle=False,collate_fn=collate_batch)

    # Model
    model = LSTMEntityModel(
        vocab_size=len(stoi),
        embed_dim=EMBED_DIM,
        hidden_size=hidden_size,
        num_classes=num_classes,
        embedding_weights=embedding_weights
    ).to(device)
    # override dropout
    model.fc[2].p = dropout_rate  # assuming fc = [Linear,ReLU,Dropout,Linear]

    optimizer = torch.optim.Adam(model.parameters(), lr=lr)
    criterion = nn.CrossEntropyLoss()

    # One-epoch train with tqdm
    model.train()
    train_bar = tqdm(tl, desc=f"[Trial {trial.number}] Train", leave=False)
    for texts, ents, labels in train_bar:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        optimizer.zero_grad()
        out = model(texts, ents)
        loss = criterion(out, labels)
        loss.backward()
        optimizer.step()
        train_bar.set_postfix(loss=f"{loss.item():.4f}")

    # One-epoch validation with tqdm
    model.eval()
    val_bar = tqdm(vl, desc=f"[Trial {trial.number}] Val  ", leave=False)
    preds, trues = [], []
    for texts, ents, labels in val_bar:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        out = model(texts, ents)
        batch_preds = out.argmax(1).cpu().tolist()
        preds += batch_preds
        trues += labels.cpu().tolist()
        val_bar.set_postfix(acc=f"{accuracy_score(trues, preds):.4f}")

    acc = accuracy_score(trues, preds)
    trial.report(acc, step=0)
    return acc

study_lstm = optuna.create_study(direction="maximize")
study_lstm.optimize(objective_lstm, n_trials=20)

print("✅ LSTM best params:", study_lstm.best_params)

[I 2025-07-24 19:37:04,223] A new study created in memory with name: no-name-3639e8d8-7c1d-45c1-809c-31f7208b60dd
/tmp/ipython-input-22-2602010146.py:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)


[Trial 0] Train:   0%|          | 0/3700 [00:00<?, ?it/s]

[Trial 0] Val  :   0%|          | 0/925 [00:00<?, ?it/s]

[I 2025-07-24 19:37:54,930] Trial 0 finished with value: 0.5822690722346104 and parameters: {'hidden_size': 64, 'dropout_rate': 0.4436469208538234, 'lr': 0.0001511028702516347, 'batch_size': 16}. Best is trial 0 with value: 0.5822690722346104.
/tmp/ipython-input-22-2602010146.py:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)


[Trial 1] Train:   0%|          | 0/3700 [00:00<?, ?it/s]

...

[I 2025-07-24 19:53:04,637] Trial 18 finished with value: 0.5174673964457058 and parameters: {'hidden_size': 256, 'dropout_rate': 0.546366828157785, 'lr': 0.009311544453691234, 'batch_size': 32}. Best is trial 14 with value: 0.6533549564159741.
/tmp/ipython-input-22-2602010146.py:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)


[Trial 19] Train:   0%|          | 0/1850 [00:00<?, ?it/s]

[Trial 19] Val  :   0%|          | 0/463 [00:00<?, ?it/s]

[I 2025-07-24 19:53:42,156] Trial 19 finished with value: 0.6378133657679573 and parameters: {'hidden_size': 128, 'dropout_rate': 0.37444575659575025, 'lr': 0.0014331893701950264, 'batch_size': 32}. Best is trial 14 with value: 0.6533549564159741.


✅ LSTM best params: {'hidden_size': 256, 'dropout_rate': 0.5065271508093174, 'lr': 0.001993763820335005, 'batch_size': 32}


In [ ]:
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score
from tqdm.auto import tqdm

# 1) Device & DataLoader’lar hazır
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True,  collate_fn=collate_batch, pin_memory=True)
val_loader   = DataLoader(val_dataset,   batch_size=32, shuffle=False, collate_fn=collate_batch, pin_memory=True)

# 2) Model ve optim
model = LSTMEntityModel(len(stoi), EMBED_DIM, 256, num_classes, embedding_weights).to(device)
model.fc[2].p = 0.5065
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.0019938)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode="max", factor=0.5, patience=3, verbose=True)

# 3) EarlyStopping ayarları
best_val_acc = 0.0
patience, counter = 5, 0
NUM_EPOCHS = 30

for epoch in range(1, NUM_EPOCHS+1):
    # — TRAIN —
    model.train()
    running_loss = 0.0
    for texts, ents, labels in train_loader:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        optimizer.zero_grad()
        out = model(texts, ents)
        loss = criterion(out, labels)
        loss.backward()
        optimizer.step()
        running_loss += loss.item() * texts.size(0)
    avg_train_loss = running_loss / len(train_loader.dataset)

    # — VALIDATION —
    model.eval()
    all_preds, all_labels, val_loss = [], [], 0.0
    with torch.no_grad():
        for texts, ents, labels in val_loader:
            texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
            out = model(texts, ents)
            val_loss += criterion(out, labels).item() * texts.size(0)
            all_preds.extend(out.argmax(1).cpu().tolist())
            all_labels.extend(labels.cpu().tolist())
    avg_val_loss = val_loss / len(val_loader.dataset)
    val_acc = accuracy_score(all_labels, all_preds)

    # LR scheduler
    scheduler.step(val_acc)

    # EarlyStopping kontrolleri
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        torch.save(model.state_dict(), "best_lstm_entity_es.pt")
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print(f"\nEarly stopping at epoch {epoch} (no improvement in {patience} epochs).")
            break

    # Epoch özeti
    print(f"Epoch {epoch:02d} | "
          f"Train Loss: {avg_train_loss:.4f} | "
          f"Val Loss: {avg_val_loss:.4f} | "
          f"Val Acc: {val_acc:.4f}")

print(f"\n🎉 Best Val Acc: {best_val_acc:.4f}")


/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "


Epoch 01 | Train Loss: 1.0182 | Val Loss: 0.8816 | Val Acc: 0.6402
Epoch 02 | Train Loss: 0.7508 | Val Loss: 0.6594 | Val Acc: 0.7445
Epoch 03 | Train Loss: 0.4816 | Val Loss: 0.5460 | Val Acc: 0.8044
Epoch 04 | Train Loss: 0.3179 | Val Loss: 0.5251 | Val Acc: 0.8239
Epoch 05 | Train Loss: 0.2424 | Val Loss: 0.5467 | Val Acc: 0.8331
Epoch 06 | Train Loss: 0.2040 | Val Loss: 0.5669 | Val Acc: 0.8404
Epoch 07 | Train Loss: 0.1784 | Val Loss: 0.5728 | Val Acc: 0.8448
Epoch 08 | Train Loss: 0.1669 | Val Loss: 0.5958 | Val Acc: 0.8509
Epoch 09 | Train Loss: 0.1566 | Val Loss: 0.6213 | Val Acc: 0.8406
Epoch 10 | Train Loss: 0.1574 | Val Loss: 0.6170 | Val Acc: 0.8400
Epoch 11 | Train Loss: 0.1264 | Val Loss: 0.6536 | Val Acc: 0.8509
Epoch 12 | Train Loss: 0.1233 | Val Loss: 0.6569 | Val Acc: 0.8473
Epoch 13 | Train Loss: 0.0782 | Val Loss: 0.7026 | Val Acc: 0.8625
Epoch 14 | Train Loss: 0.0609 | Val Loss: 0.7991 | Val Acc: 0.8576
Epoch 15 | Train Loss: 0.0667 | Val Loss: 0.7864 | Val Acc: 0.

In [ ]:
# 2) GRUEntityModel Hyperopt
import optuna
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score

def objective_gru(trial):
    hidden_size  = trial.suggest_categorical("hidden_size", [64, 128, 256])
    dropout_rate = trial.suggest_float("dropout_rate", 0.2, 0.6)
    lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)
    batch_size   = trial.suggest_categorical("batch_size", [16, 32, 64])

    tl = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, collate_fn=collate_batch)
    vl = DataLoader(val_dataset,   batch_size=batch_size, shuffle=False,collate_fn=collate_batch)

    model = GRUEntityModel(
        vocab_size=len(stoi),
        embed_dim=EMBED_DIM,
        hidden_size=hidden_size,
        num_classes=num_classes,
        embedding_weights=embedding_weights
    ).to(device)
    model.fc[2].p = dropout_rate  # assuming fc = [Linear,ReLU,Dropout,Linear]

    optimizer = torch.optim.Adam(model.parameters(), lr=lr)
    criterion = nn.CrossEntropyLoss()

    model.train()
    for texts, ents, labels in tl:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        optimizer.zero_grad()
        out = model(texts, ents)
        loss = criterion(out, labels)
        loss.backward()
        optimizer.step()

    model.eval()
    preds, trues = [], []
    with torch.no_grad():
        for texts, ents, labels in vl:
            texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
            out = model(texts, ents)
            preds += out.argmax(1).cpu().tolist()
            trues += labels.cpu().tolist()

    return accuracy_score(trues, preds)

study_gru = optuna.create_study(direction="maximize")
study_gru.optimize(objective_gru, n_trials=20)
print("GRU best params:", study_gru.best_params)


[I 2025-07-24 20:19:36,336] A new study created in memory with name: no-name-f7ca888d-90e1-4d69-ad11-3390a9c2ea81
/tmp/ipython-input-24-4066616947.py:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)
[I 2025-07-24 20:19:58,318] Trial 0 finished with value: 0.6379485100344617 and parameters: {'hidden_size': 64, 'dropout_rate': 0.3993863908980839, 'lr': 0.0038650511673201608, 'batch_size': 32}. Best is trial 0 with value: 0.6379485100344617.
/tmp/ipython-input-24-4066616947.py:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)
[I 2025-07-24 20:20:27,936] Tria

GRU best params: {'hidden_size': 256, 'dropout_rate': 0.221748925839171, 'lr': 0.0037852770832322367, 'batch_size': 64}


In [ ]:
# Gerekli kütüphaneler
!pip install tqdm

import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score
from tqdm.auto import tqdm

# 1) Device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# 2) DataLoader’lar
BATCH_SIZE = 64
train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True,
                          collate_fn=collate_batch, pin_memory=True)
val_loader   = DataLoader(val_dataset,   batch_size=BATCH_SIZE, shuffle=False,
                          collate_fn=collate_batch, pin_memory=True)

# 3) Model
model = GRUEntityModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    hidden_size=256,              # Optuna’dan
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)
model.fc[2].p = 0.221748925839171   # Dropout

# 4) Loss, Optimizer, Scheduler
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.0037852770832322367)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode="max", factor=0.5, patience=3, verbose=True
)

# 5) EarlyStopping ayarları
best_val_acc = 0.0
patience, counter = 5, 0
NUM_EPOCHS = 30

for epoch in range(1, NUM_EPOCHS+1):
    # — TRAIN —
    model.train()
    running_loss = 0.0
    processed = 0
    train_bar = tqdm(train_loader, desc=f"[Epoch {epoch}/{NUM_EPOCHS}] Train", leave=False)
    for texts, ents, labels in train_bar:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        optimizer.zero_grad()
        out = model(texts, ents)
        loss = criterion(out, labels)
        loss.backward()
        optimizer.step()

        batch_size = texts.size(0)
        running_loss += loss.item() * batch_size
        processed += batch_size
        avg_loss = running_loss / processed
        train_bar.set_postfix(loss=f"{avg_loss:.4f}")

    avg_train_loss = running_loss / len(train_loader.dataset)

    # — VALIDATION —
    model.eval()
    all_preds, all_labels, val_loss = [], [], 0.0
    processed_val = 0
    val_bar = tqdm(val_loader, desc=f"[Epoch {epoch}/{NUM_EPOCHS}] Val  ", leave=False)
    with torch.no_grad():
        for texts, ents, labels in val_bar:
            texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
            out = model(texts, ents)
            loss = criterion(out, labels)

            batch_size = texts.size(0)
            val_loss += loss.item() * batch_size
            processed_val += batch_size

            preds = out.argmax(dim=1).cpu().tolist()
            all_preds.extend(preds)
            all_labels.extend(labels.cpu().tolist())

            avg_acc = accuracy_score(all_labels, all_preds)
            val_bar.set_postfix(acc=f"{avg_acc:.4f}")

    avg_val_loss = val_loss / len(val_loader.dataset)
    val_acc = accuracy_score(all_labels, all_preds)

    # — Scheduler & EarlyStopping —
    scheduler.step(val_acc)
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        torch.save(model.state_dict(), "best_gru_entity_optimized.pt")
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print(f"\nEarly stopping at epoch {epoch} (no improvement in {patience} epochs).")
            break

    # — Epoch özeti —
    print(f"Epoch {epoch:02d} | "
          f"Train Loss: {avg_train_loss:.4f} | "
          f"Val Loss: {avg_val_loss:.4f} | "
          f"Val Acc: {val_acc:.4f}")

print(f"\n🎉 Best Val Acc: {best_val_acc:.4f}")
print("Optimized GRU weights saved to best_gru_entity_optimized.pt")


Using device: cuda


[Epoch 1/30] Train:   0%|          | 0/925 [00:00<?, ?it/s]

[Epoch 1/30] Val  :   0%|          | 0/232 [00:00<?, ?it/s]

Epoch 01 | Train Loss: 0.9783 | Val Loss: 0.7961 | Val Acc: 0.6838


[Epoch 2/30] Train:   0%|          | 0/925 [00:00<?, ?it/s]

...

[Epoch 7/30] Val  :   0%|          | 0/232 [00:00<?, ?it/s]

Epoch 07 | Train Loss: 1.0158 | Val Loss: 1.0173 | Val Acc: 0.5787


[Epoch 8/30] Train:   0%|          | 0/925 [00:00<?, ?it/s]

[Epoch 8/30] Val  :   0%|          | 0/232 [00:00<?, ?it/s]


Early stopping at epoch 8 (no improvement in 5 epochs).

🎉 Best Val Acc: 0.7332
Optimized GRU weights saved to best_gru_entity_optimized.pt


In [ ]:
# 3) CNN+LSTM Hybrid Hyperopt
import optuna
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score

def objective_cnnlstm(trial):
    num_filters  = trial.suggest_categorical("num_filters", [50, 100, 150])
    filter_size  = trial.suggest_categorical("filter_size", [3, 5, 7])
    hidden_size  = trial.suggest_categorical("hidden_size", [64, 128, 256])
    dropout_rate = trial.suggest_float("dropout_rate", 0.2, 0.6)
    lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)
    batch_size   = trial.suggest_categorical("batch_size", [16, 32, 64])

    tl = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, collate_fn=collate_batch)
    vl = DataLoader(val_dataset,   batch_size=batch_size, shuffle=False,collate_fn=collate_batch)

    model = CNNLSTMEntityModel(
        vocab_size=len(stoi),
        embed_dim=EMBED_DIM,
        num_filters=num_filters,
        filter_size=filter_size,
        hidden_size=hidden_size,
        num_classes=num_classes,
        embedding_weights=embedding_weights
    ).to(device)
    model.fc[2].p = dropout_rate  # assuming fc = [Linear,ReLU,Dropout,Linear]

    optimizer = torch.optim.Adam(model.parameters(), lr=lr)
    criterion = nn.CrossEntropyLoss()

    model.train()
    for texts, ents, labels in tl:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        optimizer.zero_grad()
        out = model(texts, ents)
        loss = criterion(out, labels)
        loss.backward()
        optimizer.step()

    model.eval()
    preds, trues = [], []
    with torch.no_grad():
        for texts, ents, labels in vl:
            texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
            out = model(texts, ents)
            preds += out.argmax(1).cpu().tolist()
            trues += labels.cpu().tolist()

    return accuracy_score(trues, preds)

study_cnnlstm = optuna.create_study(direction="maximize")
study_cnnlstm.optimize(objective_cnnlstm, n_trials=20)
print("CNN+LSTM best params:", study_cnnlstm.best_params)


[I 2025-07-24 20:35:57,004] A new study created in memory with name: no-name-245ad272-b188-4052-a0ca-efb43a42d15d
/tmp/ipython-input-27-3341615491.py:13: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr           = trial.suggest_loguniform("lr", 1e-4, 1e-2)
[I 2025-07-24 20:36:38,844] Trial 0 finished with value: 0.5964592202175822 and parameters: {'num_filters': 100, 'filter_size': 3, 'hidden_size': 128, 'dropout_rate': 0.36379054590761956, 'lr': 0.001616450783150156, 'batch_size': 16}. Best is trial 0 with value: 0.5964592202175822.
/tmp/ipython-input-27-3341615491.py:13: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr           = trial.suggest_loguniform("lr", 1e-4,

CNN+LSTM best params: {'num_filters': 150, 'filter_size': 3, 'hidden_size': 256, 'dropout_rate': 0.4916032054138277, 'lr': 0.0006594012615248541, 'batch_size': 32}


In [ ]:
# CNN+LSTM Optimized Training Script
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score
from tqdm.auto import tqdm

# 1) Device setup
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# 2) DataLoader setup with optimized batch_size
BATCH_SIZE = 32
train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True,
                          collate_fn=collate_batch, pin_memory=True)
val_loader   = DataLoader(val_dataset,   batch_size=BATCH_SIZE, shuffle=False,
                          collate_fn=collate_batch, pin_memory=True)

# 3) Model initialization with optimized hyperparameters
model = CNNLSTMEntityModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    num_filters=150,
    filter_size=3,
    hidden_size=256,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)

# Set optimized dropout rate on the fc layer (assumed fc[2] is Dropout)
model.fc[2].p = 0.4916032054138277

# 4) Loss, optimizer, scheduler
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.0006594012615248541)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode="max", factor=0.5, patience=3, verbose=True
)

# 5) EarlyStopping parameters
best_val_acc = 0.0
patience, counter = 5, 0
NUM_EPOCHS = 30

for epoch in range(1, NUM_EPOCHS + 1):
    # Training
    model.train()
    train_loss = 0.0
    processed = 0
    train_bar = tqdm(train_loader, desc=f"[Epoch {epoch}/{NUM_EPOCHS}] Train", leave=False)
    for texts, ents, labels in train_bar:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        optimizer.zero_grad()
        outputs = model(texts, ents)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        batch_size = texts.size(0)
        train_loss += loss.item() * batch_size
        processed += batch_size
        avg_loss = train_loss / processed
        train_bar.set_postfix(loss=f"{avg_loss:.4f}")

    avg_train_loss = train_loss / len(train_loader.dataset)

    # Validation
    model.eval()
    val_loss = 0.0
    all_preds, all_labels = [], []
    val_bar = tqdm(val_loader, desc=f"[Epoch {epoch}/{NUM_EPOCHS}] Val  ", leave=False)
    with torch.no_grad():
        for texts, ents, labels in val_bar:
            texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
            outputs = model(texts, ents)
            loss = criterion(outputs, labels)

            batch_size = texts.size(0)
            val_loss += loss.item() * batch_size
            preds = outputs.argmax(dim=1).cpu().tolist()
            all_preds.extend(preds)
            all_labels.extend(labels.cpu().tolist())

            avg_acc = accuracy_score(all_labels, all_preds)
            val_bar.set_postfix(acc=f"{avg_acc:.4f}")

    avg_val_loss = val_loss / len(val_loader.dataset)
    val_acc = accuracy_score(all_labels, all_preds)

    # Scheduler & EarlyStopping
    scheduler.step(val_acc)
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        torch.save(model.state_dict(), "best_cnnlstm_entity_optimized.pt")
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print(f"\nEarly stopping at epoch {epoch} (no improvement in {patience} epochs).")
            break

    # Epoch summary
    print(f"Epoch {epoch:02d} | "
          f"Train Loss: {avg_train_loss:.4f} | "
          f"Val Loss: {avg_val_loss:.4f} | "
          f"Val Acc: {val_acc:.4f}")

print(f"\n🎉 Best Val Acc: {best_val_acc:.4f}")
print("Optimized CNN+LSTM weights saved to best_cnnlstm_entity_optimized.pt")

Using device: cuda


/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "


[Epoch 1/30] Train:   0%|          | 0/1850 [00:00<?, ?it/s]

[Epoch 1/30] Val  :   0%|          | 0/463 [00:00<?, ?it/s]

Epoch 01 | Train Loss: 1.0442 | Val Loss: 0.9437 | Val Acc: 0.6144


...

[Epoch 25/30] Val  :   0%|          | 0/463 [00:00<?, ?it/s]

Epoch 25 | Train Loss: 0.0376 | Val Loss: 1.0193 | Val Acc: 0.8497


[Epoch 26/30] Train:   0%|          | 0/1850 [00:00<?, ?it/s]

[Epoch 26/30] Val  :   0%|          | 0/463 [00:00<?, ?it/s]


Early stopping at epoch 26 (no improvement in 5 epochs).

🎉 Best Val Acc: 0.8519
Optimized CNN+LSTM weights saved to best_cnnlstm_entity_optimized.pt


In [ ]:
!pip install transformers tqdm

In [ ]:
# Downgrade NumPy to a 1.x series and upgrade Transformers
!pip install "numpy<2" --upgrade
!pip install --upgrade transformers


  Using cached transformers-4.53.3-py3-none-any.whl.metadata (40 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.8/10.8 MB 42.8 MB/s eta 0:00:00
  Attempting uninstall: transformers
    Found existing installation: transformers 4.53.2
    Uninstalling transformers-4.53.2:
      Successfully uninstalled transformers-4.53.2


In [ ]:
!pip uninstall -y transformers
!pip install transformers==4.31.0  # or another 4.x release that includes the sequence‐classification classes


Found existing installation: transformers 4.53.2
Uninstalling transformers-4.53.2:
  Successfully uninstalled transformers-4.53.2
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.9/116.9 kB 2.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 15.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 14.0 MB/s eta 0:00:00
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.21.2
    Uninstalling tokenizers-0.21.2:
      Successfully uninstalled tokenizers-0.21.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchtune 0.6.1 requires torchdata==0.11.0, but you have torchdata 0.7.1 which is incompatible.
sentence-transformers 4.1.0 requires transformers<5.0.0,>=4.41.0, but you have transformers 4.31.0 which is incompatible.


In [13]:
import torch
from torch.utils.data import Dataset, DataLoader, random_split
from transformers import BertTokenizerFast, AutoConfig, AutoModelForSequenceClassification, get_linear_schedule_with_warmup
from torch.optim import AdamW
from sklearn.metrics import accuracy_score
from tqdm.auto import tqdm

# 2) Dataset definition
class BERTEnglishEntityDataset(Dataset):
    def __init__(self, df, tokenizer, max_len=128):
        self.df = df.reset_index(drop=True)
        self.tok = tokenizer
        self.max_len = max_len

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        text, ent = str(row['tweet']), str(row['entity'])
        marked = text.replace(ent, f"[E_START] {ent} [E_END]")
        enc = self.tok(
            marked,
            padding='max_length',
            truncation=True,
            max_length=self.max_len,
            return_tensors='pt'
        )
        return {
            'input_ids':      enc['input_ids'].squeeze(0),
            'attention_mask': enc['attention_mask'].squeeze(0),
            'labels':         torch.tensor(row['label_idx'], dtype=torch.long)
        }

# 3) Train/Validation split
train_size = int(0.8 * len(df))
val_size   = len(df) - train_size
train_df, val_df = random_split(
    df, [train_size, val_size],
    generator=torch.Generator().manual_seed(42)
)

# 4) Tokenizer & DataLoader setup
tokenizer = BertTokenizerFast.from_pretrained("bert-base-uncased")
train_ds = BERTEnglishEntityDataset(train_df.dataset.iloc[train_df.indices], tokenizer)
val_ds   = BERTEnglishEntityDataset(val_df.dataset.iloc[val_df.indices],     tokenizer)

train_loader = DataLoader(train_ds, batch_size=16, shuffle=True)
val_loader   = DataLoader(val_ds,   batch_size=16, shuffle=False)

# 5) Model, optimizer, scheduler
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
config = AutoConfig.from_pretrained("bert-base-uncased", num_labels=num_classes)
model  = AutoModelForSequenceClassification.from_pretrained(
    "bert-base-uncased", config=config
).to(device)

optimizer = AdamW(model.parameters(), lr=2e-5, weight_decay=0.01)
total_steps = len(train_loader) * 3
scheduler = get_linear_schedule_with_warmup(
    optimizer,
    num_warmup_steps=int(0.1 * total_steps),
    num_training_steps=total_steps
)

# 6) Training loop with tqdm, early stopping & checkpointing
best_val_acc, patience, counter = 0.0, 3, 0
NUM_EPOCHS = 3

for epoch in range(1, NUM_EPOCHS + 1):
    # Training
    model.train()
    train_loss = 0.0
    for batch in tqdm(train_loader, desc=f"Epoch {epoch}/{NUM_EPOCHS} [Train]"):
        optimizer.zero_grad()
        batch = {k: v.to(device) for k, v in batch.items()}
        outputs = model(**batch)
        loss = outputs.loss
        loss.backward()
        optimizer.step()
        scheduler.step()
        train_loss += loss.item() * batch['input_ids'].size(0)
    avg_train = train_loss / len(train_loader.dataset)

    # Validation
    model.eval()
    all_preds, all_labels = [], []
    for batch in tqdm(val_loader, desc=f"Epoch {epoch}/{NUM_EPOCHS} [Val]"):
        inputs = {k: v.to(device) for k, v in batch.items() if k != 'labels'}
        labels = batch['labels'].to(device)
        logits = model(**inputs).logits
        preds = logits.argmax(dim=1).cpu().tolist()
        all_preds.extend(preds)
        all_labels.extend(labels.cpu().tolist())
    val_acc = accuracy_score(all_labels, all_preds)

    print(f"Epoch {epoch:02d} | Train Loss: {avg_train:.4f} | Val Acc: {val_acc:.4f}")

    # Early stopping & checkpoint
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        model.save_pretrained("best_bert_english_model")
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print(f"Early stopping at epoch {epoch}.")
            break

print(f"\n🎯 Best BERT‑EN Val Acc: {best_val_acc:.4f}")
print("Model and tokenizer saved to ./best_bert_english_model")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/file_download.py:943: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

...

Epoch 2/3 [Val]:   0%|          | 0/925 [00:00<?, ?it/s]

Epoch 02 | Train Loss: 0.3336 | Val Acc: 0.8948


Epoch 3/3 [Train]:   0%|          | 0/3700 [00:00<?, ?it/s]

Epoch 3/3 [Val]:   0%|          | 0/925 [00:00<?, ?it/s]

Epoch 03 | Train Loss: 0.1344 | Val Acc: 0.9132

🎯 Best BERT‑EN Val Acc: 0.9132
Model and tokenizer saved to ./best_bert_english_model


## Real Test Phase

In [38]:
import torch
import torch.nn as nn

class LSTMEntityModel(nn.Module):
    def __init__(self, vocab_size, embed_dim, hidden_size, num_classes, embedding_weights):
        super().__init__()
        self.embedding = nn.Embedding.from_pretrained(
            embedding_weights, freeze=True, padding_idx=stoi["<pad>"]
        )
        self.lstm = nn.LSTM(embed_dim, hidden_size, batch_first=True, bidirectional=True)
        self.fc = nn.Sequential(
            nn.Linear(2*hidden_size + embed_dim, hidden_size),
            nn.ReLU(),
            nn.Dropout(0.5),
            nn.Linear(hidden_size, num_classes)
        )

    def forward(self, text, ent):
        emb_t = self.embedding(text)
        _, (h_n, _) = self.lstm(emb_t)
        txt_repr = torch.cat([h_n[0], h_n[1]],1)
        ent_repr = self.embedding(ent).mean(1)
        x = torch.cat([txt_repr, ent_repr],1)
        return self.fc(x)

class GRUEntityModel(nn.Module):
    def __init__(self, vocab_size, embed_dim, hidden_size, num_classes, embedding_weights):
        super().__init__()
        self.embedding = nn.Embedding.from_pretrained(
            embedding_weights, freeze=True, padding_idx=stoi["<pad>"]
        )
        self.gru = nn.GRU(embed_dim, hidden_size, batch_first=True, bidirectional=True)
        self.fc  = nn.Sequential(
            nn.Linear(2*hidden_size + embed_dim, hidden_size),
            nn.ReLU(), nn.Dropout(0.5),
            nn.Linear(hidden_size, num_classes)
        )

    def forward(self, text, ent):
        emb = self.embedding(text)
        _, h_n = self.gru(emb)
        txt = torch.cat([h_n[0], h_n[1]], dim=1)
        ent_repr = self.embedding(ent).mean(1)
        return self.fc(torch.cat([txt, ent_repr], dim=1))

class CNNLSTMEntityModel(nn.Module):
    def __init__(self, vocab_size, embed_dim, num_filters, filter_size, hidden_size, num_classes, embedding_weights):
        super().__init__()
        self.embedding = nn.Embedding.from_pretrained(
            embedding_weights, freeze=True, padding_idx=stoi["<pad>"]
        )
        self.conv = nn.Conv1d(embed_dim, num_filters, kernel_size=filter_size, padding=filter_size//2)
        self.lstm = nn.LSTM(num_filters, hidden_size, batch_first=True, bidirectional=True)
        self.fc   = nn.Sequential(
            nn.Linear(2*hidden_size + embed_dim, hidden_size),
            nn.ReLU(), nn.Dropout(0.5),
            nn.Linear(hidden_size, num_classes)
        )

    def forward(self, text, ent):
        emb = self.embedding(text).transpose(1,2)
        conv = self.conv(emb).transpose(1,2)
        _, (h_n, _) = self.lstm(conv)
        txt = torch.cat([h_n[0], h_n[1]], dim=1)
        ent_repr = self.embedding(ent).mean(1)
        return self.fc(torch.cat([txt, ent_repr], dim=1))

class CNNTextModel(nn.Module):
    def __init__(self, vocab_size, embed_dim, num_filters, filter_sizes, hidden_size, num_classes, embedding_weights):
        super().__init__()
        self.embedding = nn.Embedding.from_pretrained(
            embedding_weights, freeze=True, padding_idx=stoi["<pad>"]
        )
        self.convs = nn.ModuleList([
            nn.Conv1d(embed_dim, num_filters, fs, padding=fs//2) for fs in filter_sizes
        ])
        self.fc = nn.Sequential(
            nn.Linear(len(filter_sizes)*num_filters, hidden_size),
            nn.ReLU(), nn.Dropout(0.5),
            nn.Linear(hidden_size, num_classes)
        )

    def forward(self, text, _ent=None):
        emb = self.embedding(text).transpose(1,2)
        convs = [torch.relu(conv(emb)).max(dim=2)[0] for conv in self.convs]
        feat = torch.cat(convs, dim=1)
        return self.fc(feat)


In [30]:
df

index       entity sentiment  \
0       2401  Borderlands  Positive   
1       2401  Borderlands  Positive   
2       2401  Borderlands  Positive   
3       2401  Borderlands  Positive   
4       2401  Borderlands  Positive   
...      ...          ...       ...   
73990   9200       Nvidia  Positive   
73991   9200       Nvidia  Positive   
73992   9200       Nvidia  Positive   
73993   9200       Nvidia  Positive   
73994   9200       Nvidia  Positive   

                                                   tweet  
0      I am coming to the borders and I will kill you...  
1      im getting on borderlands and i will kill you ...  
2      im coming on borderlands and i will murder you...  
3      im getting on borderlands 2 and i will murder ...  
4      im getting into borderlands and i can murder y...  
...                                                  ...  
73990  Just realized that the Windows partition of my...  
73991  Just realized that my Mac window partition is ...  
73992  Just realized the windows partition of my Mac ...  
73993  Just realized between the windows partition of...  
73994  Just like the windows partition of my Mac is l...  

[73995 rows x 4 columns]

In [35]:
# 2) Prepare & split data into train/val/test
full_df = df.dropna(subset=['tweet','entity','label_idx']).reset_index(drop=True)
train_df, temp_df = train_test_split(
    full_df,
    test_size=0.20,               # %20 → val+test
    stratify=full_df['label_idx'],
    random_state=42
)
val_df, test_df = train_test_split(
    temp_df,
    test_size=0.50,               # temp’in yarısı test, yarısı val
    stratify=temp_df['label_idx'],
    random_state=42
)

# 3) Dataset + collate_fn
class EntityDataset(Dataset):
    def __init__(self, df):
        self.df = df
    def __len__(self):
        return len(self.df)
    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        text = mark_entity(row['tweet'], row['entity'])
        tok_text = [stoi.get(t, stoi["<unk>"]) for t in tokenize(text)]
        tok_ent  = [stoi.get(t, stoi["<unk>"]) for t in tokenize(str(row['entity']))]
        label    = int(row['label_idx'])
        return torch.tensor(tok_text), torch.tensor(tok_ent), torch.tensor(label)

def collate_fn(batch):
    texts, ents, labels = zip(*batch)
    texts_p = pad_sequence(texts, batch_first=True, padding_value=stoi["<pad>"])
    ents_p  = pad_sequence(ents,  batch_first=True, padding_value=stoi["<pad>"])
    return texts_p.long(), ents_p.long(), torch.stack(labels).long()

# 4) DataLoaders
train_loader = DataLoader(EntityDataset(train_df), batch_size=BATCH_SIZE,
                          shuffle=True,  collate_fn=collate_fn,
                          pin_memory=True, num_workers=4)
val_loader   = DataLoader(EntityDataset(val_df),   batch_size=BATCH_SIZE,
                          shuffle=False, collate_fn=collate_fn,
                          pin_memory=True, num_workers=2)
test_loader  = DataLoader(EntityDataset(test_df),  batch_size=BATCH_SIZE,
                          shuffle=False, collate_fn=collate_fn,
                          pin_memory=True, num_workers=2)

### LSTM

In [61]:
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from collections import Counter
from tqdm.auto import tqdm

# ——— 1) Label → idx eşlemesini doğru kur ———
label_order = ["Irrelevant","Negative","Neutral","Positive"]
label_to_idx = {lab:i for i,lab in enumerate(label_order)}
full_df['label_idx'] = full_df['sentiment'].map(label_to_idx)
num_classes = len(label_order)

# ——— 2) Train/Val/Test split (stratify ile) ———
train_df, temp_df = train_test_split(
    full_df, test_size=0.20,
    stratify=full_df['label_idx'],
    random_state=42
)
val_df, test_df = train_test_split(
    temp_df, test_size=0.50,
    stratify=temp_df['label_idx'],
    random_state=42
)

# ——— Dataset tanımı ———
class EntityDataset(Dataset):
    def __init__(self, df): self.df = df
    def __len__(self):     return len(self.df)
    def __getitem__(self, i):
        row = self.df.iloc[i]
        txt = [stoi.get(t,stoi["<unk>"]) for t in tokenize(mark_entity(row['tweet'], row['entity']))]
        ent = [stoi.get(t,stoi["<unk>"]) for t in tokenize(str(row['entity']))]
        lbl = int(row['label_idx'])  # <-- burayı böyle değiştir
        return (
            torch.tensor(txt, dtype=torch.long),
            torch.tensor(ent, dtype=torch.long),
            torch.tensor(lbl, dtype=torch.long)
        )

# ——— Distribution check ———
from collections import Counter
print("Train label dağılımı:", Counter(train_df['label_idx']))
print("Val   label dağılımı:", Counter(val_df['label_idx']))


def collate_fn(batch):
    texts, ents, labs = zip(*batch)
    return (pad_sequence(texts, batch_first=True, padding_value=stoi["<pad>"]).long(),
            pad_sequence(ents,  batch_first=True, padding_value=stoi["<pad>"]).long(),
            torch.stack(labs).long())

# ——— 4) DataLoader’lar ———
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
train_loader = DataLoader(EntityDataset(train_df), batch_size=32, shuffle=True,
                          collate_fn=collate_fn, pin_memory=True, num_workers=4)
val_loader   = DataLoader(EntityDataset(val_df),   batch_size=32, shuffle=False,
                          collate_fn=collate_fn, pin_memory=True, num_workers=2)

# ——— 5) Sanity check dağılımlar ———
print("Train label dağılımı:", Counter([lab for *_,lab in train_loader.dataset]))
print("Val   label dağılımı:", Counter([lab for *_,lab in val_loader.dataset]))

# ——— 6) Model + Eğitim döngüsü ———
model = LSTMEntityModel(len(stoi), EMBED_DIM, 256, num_classes, embedding_weights).to(device)
model.fc[2].p = 0.5065
opt   = torch.optim.Adam(model.parameters(), lr=0.0019938)
crit  = nn.CrossEntropyLoss()
sched = torch.optim.lr_scheduler.ReduceLROnPlateau(opt, mode="max", factor=0.5, patience=3, verbose=True)

best_val_acc, counter = 0, 0
for epoch in range(1,31):
    model.train()
    tloss=0
    for t,e,l in train_loader:
        t,e,l = t.to(device), e.to(device), l.to(device)
        opt.zero_grad(); out=model(t,e); loss=crit(out,l)
        loss.backward(); opt.step()
        tloss += loss.item()*t.size(0)
    model.eval()
    vloss, preds, trues = 0, [], []
    with torch.no_grad():
        for t,e,l in val_loader:
            t,e,l = t.to(device), e.to(device), l.to(device)
            o = model(t,e)
            vloss += crit(o,l).item()*t.size(0)
            preds += o.argmax(1).cpu().tolist()
            trues += l.cpu().tolist()
    val_acc = accuracy_score(trues, preds)
    sched.step(val_acc)
    if val_acc>best_val_acc:
        best_val_acc, counter = val_acc, 0
        torch.save(model.state_dict(), "best_lstm_entity_test_final_fixed.pt")
    else:
        counter+=1
        if counter>=5:
            print(f"Early stop at epoch {epoch}")
            break
    print(f"Epoch {epoch:02d} | TrainLoss: {tloss/len(train_loader.dataset):.4f} | ValAcc: {val_acc:.4f}")

print("🎯 Best Val Acc:", best_val_acc)


Train label dağılımı: Counter({1: 17886, 3: 16523, 2: 14487, 0: 10300})
Val   label dağılımı: Counter({1: 2236, 3: 2065, 2: 1810, 0: 1288})
Train label dağılımı: Counter({tensor(0): 1, tensor(3): 1, tensor(1): 1, tensor(1): 1, tensor(3): 1, tensor(2): 1, tensor(3): 1, tensor(1): 1, tensor(0): 1, tensor(1): 1, tensor(1): 1, tensor(3): 1, tensor(1): 1, tensor(1): 1, tensor(2): 1, tensor(1): 1, tensor(3): 1, tensor(1): 1, tensor(3): 1, tensor(1): 1, tensor(2): 1, tensor(0): 1, tensor(1): 1, tensor(2): 1, tensor(3): 1, tensor(3): 1, tensor(0): 1, tensor(2): 1, tensor(1): 1, tensor(1): 1, tensor(0): 1, tensor(3): 1, tensor(3): 1, tensor(2): 1, tensor(1): 1, tensor(1): 1, tensor(2): 1, tensor(1): 1, tensor(1): 1, tensor(1): 1, tensor(2): 1, tensor(1): 1, tensor(2): 1, tensor(0): 1, tensor(2): 1, tensor(3): 1, tensor(1): 1, tensor(1): 1, tensor(0): 1, tensor(3): 1, tensor(0): 1, tensor(3): 1, tensor(3): 1, tensor(2): 1, tensor(2): 1, tensor(0): 1, tensor(1): 1, tensor(1): 1, tensor(3): 1, ten

/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "


Epoch 01 | TrainLoss: 1.0201 | ValAcc: 0.6528
Epoch 02 | TrainLoss: 0.7440 | ValAcc: 0.7366
Epoch 03 | TrainLoss: 0.4786 | ValAcc: 0.7956
Epoch 04 | TrainLoss: 0.3165 | ValAcc: 0.8169
Epoch 05 | TrainLoss: 0.2371 | ValAcc: 0.8355
Epoch 06 | TrainLoss: 0.2048 | ValAcc: 0.8328
Epoch 07 | TrainLoss: 0.1813 | ValAcc: 0.8421
Epoch 08 | TrainLoss: 0.1685 | ValAcc: 0.8435
Epoch 09 | TrainLoss: 0.1609 | ValAcc: 0.8439
Epoch 10 | TrainLoss: 0.1548 | ValAcc: 0.8384
Epoch 11 | TrainLoss: 0.1498 | ValAcc: 0.8480
Epoch 12 | TrainLoss: 0.1356 | ValAcc: 0.8450
Epoch 13 | TrainLoss: 0.1370 | ValAcc: 0.8443
Epoch 14 | TrainLoss: 0.1423 | ValAcc: 0.8486
Epoch 15 | TrainLoss: 0.1386 | ValAcc: 0.8423
Epoch 16 | TrainLoss: 0.1347 | ValAcc: 0.8489
Epoch 17 | TrainLoss: 0.1348 | ValAcc: 0.8458
Epoch 18 | TrainLoss: 0.1261 | ValAcc: 0.8413
Epoch 19 | TrainLoss: 0.1326 | ValAcc: 0.8465
Epoch 20 | TrainLoss: 0.1330 | ValAcc: 0.8455
Epoch 21 | TrainLoss: 0.0824 | ValAcc: 0.8617
Epoch 22 | TrainLoss: 0.0599 | Val

In [63]:
import torch
import torch.nn as nn
from sklearn.metrics import accuracy_score

# 1) Modeli yeniden tanımla ve en iyi ağırlıkları yükle
best_lstm = LSTMEntityModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    hidden_size=256,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)

state = torch.load("best_lstm_entity_test_final_fixed.pt", map_location=device)
best_lstm.load_state_dict(state)
best_lstm.eval()

# 2) Test set’inde loss & accuracy ölçümü
criterion = nn.CrossEntropyLoss()
test_loss = 0.0
all_preds, all_labels = [], []

with torch.no_grad():
    for texts, ents, labels in test_loader:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        out = best_lstm(texts, ents)
        test_loss += criterion(out, labels).item() * texts.size(0)
        all_preds.extend(out.argmax(1).cpu().tolist())
        all_labels.extend(labels.cpu().tolist())

avg_test_loss = test_loss / len(test_loader.dataset)
test_acc     = accuracy_score(all_labels, all_preds)

print(f"🔍 Test Loss: {avg_test_loss:.4f} | Test Acc: {test_acc:.4f}")


🔍 Test Loss: 0.7796 | Test Acc: 0.8536


## GRU

In [67]:
import torch
import torch.nn as nn
from sklearn.metrics import accuracy_score
from tqdm.auto import tqdm

# 1) Cihaz
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Training on:", device)

# 2) Model oluştur (constructor’da dropout_p yok)
gru = GRUEntityModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    hidden_size=256,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)
# Manuel olarak optimize ettiğin dropout değerini ayarla:
gru.fc[2].p = 0.221748925839171

# 3) Kayıp, optimizer, scheduler
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(gru.parameters(), lr=0.0037852770832322367)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode="max", factor=0.5, patience=3, verbose=True
)

# 4) EarlyStopping ayarları
best_val_acc = 0.0
patience, counter = 5, 0
NUM_EPOCHS = 30

# 5) Train + Val döngüsü
for epoch in range(1, NUM_EPOCHS+1):
    # — TRAIN —
    gru.train()
    train_loss = 0.0
    for texts, ents, labels in train_loader:
        texts, ents, labels = (
            texts.to(device, non_blocking=True),
            ents.to(device, non_blocking=True),
            labels.to(device, non_blocking=True),
        )
        optimizer.zero_grad()
        out = gru(texts, ents)
        loss = criterion(out, labels)
        loss.backward()
        optimizer.step()
        train_loss += loss.item() * texts.size(0)
    avg_train_loss = train_loss / len(train_loader.dataset)

    # — VALIDATION —
    gru.eval()
    val_loss, preds, trues = 0.0, [], []
    with torch.no_grad():
        for texts, ents, labels in val_loader:
            texts, ents, labels = (
                texts.to(device, non_blocking=True),
                ents.to(device, non_blocking=True),
                labels.to(device, non_blocking=True),
            )
            out = gru(texts, ents)
            val_loss += criterion(out, labels).item() * texts.size(0)
            preds += out.argmax(1).cpu().tolist()
            trues += labels.cpu().tolist()
    avg_val_loss = val_loss / len(val_loader.dataset)
    val_acc = accuracy_score(trues, preds)

    # — Scheduler & EarlyStopping —
    scheduler.step(val_acc)
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        torch.save(gru.state_dict(), "best_gru_entity_es.pt")
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print(f"\nEarly stopping at epoch {epoch} (no improvement for {patience} epochs).")
            break

    print(
        f"Epoch {epoch:02d} | "
        f"Train Loss: {avg_train_loss:.4f} | "
        f"Val   Loss: {avg_val_loss:.4f} | "
        f"Val   Acc: {val_acc:.4f}"
    )

print(f"\n🎯 Best GRU Val Acc: {best_val_acc:.4f}")

# 6) Test değerlendirmesi
best_gru = GRUEntityModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    hidden_size=256,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)
# Yine manuel dropout ayarı:
best_gru.fc[2].p = 0.221748925839171

# Ağırlıkları yükle
state = torch.load("best_gru_entity_final_test_es.pt", map_location=device)
best_gru.load_state_dict(state)
best_gru.eval()

# Ölçüm
test_loss, test_preds, test_trues = 0.0, [], []
with torch.no_grad():
    for texts, ents, labels in test_loader:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        out = best_gru(texts, ents)
        test_loss += criterion(out, labels).item() * texts.size(0)
        test_preds += out.argmax(1).cpu().tolist()
        test_trues += labels.cpu().tolist()

avg_test_loss = test_loss / len(test_loader.dataset)
test_acc = accuracy_score(test_trues, test_preds)
print(f"🔍 GRU Test Loss: {avg_test_loss:.4f} | Test Acc: {test_acc:.4f}")


Training on: cuda


/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "


Epoch 01 | Train Loss: 1.0069 | Val   Loss: 0.8860 | Val   Acc: 0.6386
Epoch 02 | Train Loss: 0.8666 | Val   Loss: 0.8822 | Val   Acc: 0.6444
Epoch 03 | Train Loss: 0.9117 | Val   Loss: 0.9902 | Val   Acc: 0.5883
Epoch 04 | Train Loss: 1.0082 | Val   Loss: 1.0008 | Val   Acc: 0.5759
Epoch 05 | Train Loss: 1.0207 | Val   Loss: 1.0360 | Val   Acc: 0.5571
Epoch 06 | Train Loss: 1.0518 | Val   Loss: 1.0271 | Val   Acc: 0.5690

Early stopping at epoch 7 (no improvement for 5 epochs).

🎯 Best GRU Val Acc: 0.6444
🔍 GRU Test Loss: 0.8425 | Test Acc: 0.6666


## CNN+LSTM

In [70]:
import torch
import torch.nn as nn
from sklearn.metrics import accuracy_score
from tqdm.auto import tqdm

# 1) Cihaz ayarı
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# 2) Model ve hiperparametreler
cnn_lstm = CNNLSTMEntityModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    num_filters=150,
    filter_size=3,
    hidden_size=256,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)
# Manuel dropout ayarı
cnn_lstm.fc[2].p = 0.4916032054138277

# 3) Loss, optimizer, scheduler
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(cnn_lstm.parameters(), lr=0.0006594012615248541)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode="max", factor=0.5, patience=3, verbose=True
)

# 4) EarlyStopping ayarları
best_val_acc = 0.0
patience, counter = 5, 0
NUM_EPOCHS = 30

# 5) Train + Val döngüsü
for epoch in range(1, NUM_EPOCHS+1):
    # — TRAIN —
    cnn_lstm.train()
    train_loss = 0.0
    processed = 0
    train_bar = tqdm(train_loader, desc=f"[Epoch {epoch}/{NUM_EPOCHS}] Train", leave=False)
    for texts, ents, labels in train_bar:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)

        optimizer.zero_grad()
        outputs = cnn_lstm(texts, ents)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        batch_size = texts.size(0)
        train_loss += loss.item() * batch_size
        processed += batch_size
        train_bar.set_postfix(loss=f"{train_loss/processed:.4f}")

    avg_train_loss = train_loss / len(train_loader.dataset)

    # — VALIDATION —
    cnn_lstm.eval()
    val_loss = 0.0
    all_preds, all_labels = [], []
    val_bar = tqdm(val_loader, desc=f"[Epoch {epoch}/{NUM_EPOCHS}] Val  ", leave=False)
    with torch.no_grad():
        for texts, ents, labels in val_bar:
            texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
            outputs = cnn_lstm(texts, ents)
            loss = criterion(outputs, labels)

            batch_size = texts.size(0)
            val_loss += loss.item() * batch_size
            preds = outputs.argmax(dim=1).cpu().tolist()
            all_preds.extend(preds)
            all_labels.extend(labels.cpu().tolist())

            val_bar.set_postfix(acc=f"{accuracy_score(all_labels, all_preds):.4f}")

    avg_val_loss = val_loss / len(val_loader.dataset)
    val_acc = accuracy_score(all_labels, all_preds)

    # — Scheduler & EarlyStopping —
    scheduler.step(val_acc)
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        torch.save(cnn_lstm.state_dict(), "best_cnnlstm_entity_final_test_optimized.pt")
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print(f"\nEarly stopping at epoch {epoch} (no improvement in {patience} epochs).")
            break

    print(f"Epoch {epoch:02d} | "
          f"Train Loss: {avg_train_loss:.4f} | "
          f"Val   Loss: {avg_val_loss:.4f} | "
          f"Val   Acc: {val_acc:.4f}")

print(f"\n🎉 Best Val Acc: {best_val_acc:.4f}")
print("✅ Optimized CNN+LSTM weights saved to best_cnnlstm_entity_optimized.pt")

# 6) Test değerlendirmesi
best_model = CNNLSTMEntityModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    num_filters=150,
    filter_size=3,
    hidden_size=256,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)
best_model.fc[2].p = 0.4916032054138277

# Ağırlıkları yükle
best_model.load_state_dict(torch.load("best_cnnlstm_entity_final_test_optimized.pt", map_location=device))
best_model.eval()

test_loss = 0.0
test_preds, test_trues = [], []
with torch.no_grad():
    for texts, ents, labels in test_loader:
        texts, ents, labels = texts.to(device), ents.to(device), labels.to(device)
        outputs = best_model(texts, ents)
        test_loss += criterion(outputs, labels).item() * texts.size(0)
        test_preds.extend(outputs.argmax(dim=1).cpu().tolist())
        test_trues.extend(labels.cpu().tolist())

avg_test_loss = test_loss / len(test_loader.dataset)
test_acc     = accuracy_score(test_trues, test_preds)
print(f"\n🔍 CNN+LSTM Test Loss: {avg_test_loss:.4f} | Test Acc: {test_acc:.4f}")


Using device: cuda


/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "


[Epoch 1/30] Train:   0%|          | 0/1850 [00:00<?, ?it/s]

[Epoch 1/30] Val  :   0%|          | 0/232 [00:00<?, ?it/s]

Epoch 01 | Train Loss: 1.0480 | Val   Loss: 0.9545 | Val   Acc: 0.6026


...

[Epoch 29/30] Val  :   0%|          | 0/232 [00:00<?, ?it/s]

Epoch 29 | Train Loss: 0.0358 | Val   Loss: 1.0934 | Val   Acc: 0.8473


[Epoch 30/30] Train:   0%|          | 0/1850 [00:00<?, ?it/s]

[Epoch 30/30] Val  :   0%|          | 0/232 [00:00<?, ?it/s]

Epoch 30 | Train Loss: 0.0359 | Val   Loss: 1.0834 | Val   Acc: 0.8475

🎉 Best Val Acc: 0.8543
✅ Optimized CNN+LSTM weights saved to best_cnnlstm_entity_optimized.pt

🔍 CNN+LSTM Test Loss: 1.0784 | Test Acc: 0.8496


### CNN

In [77]:
import torch
import torch.nn as nn
from sklearn.metrics import accuracy_score
from tqdm.auto import tqdm

# 1) Cihaz ve DataLoader’ların hazır olduğunu varsayıyoruz:
#    train_loader, val_loader, test_loader

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# 2) Model tanımı
model = CNNTextModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    num_filters=100,
    filter_sizes=[3,4,5],
    hidden_size=128,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode="max", factor=0.5, patience=2, verbose=True
)

# 3) EarlyStopping ayarları
best_val_acc = 0.0
patience, counter = 5, 0
NUM_EPOCHS = 10

# 4) Train + Val
for epoch in range(1, NUM_EPOCHS+1):
    # — TRAINING —
    model.train()
    train_loss = 0.0
    for texts, _, labels in tqdm(train_loader, desc=f"[CNN] Train {epoch}/{NUM_EPOCHS}", leave=False):
        texts, labels = texts.to(device), labels.to(device)
        optimizer.zero_grad()
        outputs = model(texts)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        train_loss += loss.item() * texts.size(0)
    avg_train_loss = train_loss / len(train_loader.dataset)

    # — VALIDATION —
    model.eval()
    val_preds, val_trues = [], []
    val_loss = 0.0
    with torch.no_grad():
        for texts, _, labels in tqdm(val_loader, desc=f"[CNN] Val   {epoch}/{NUM_EPOCHS}", leave=False):
            texts, labels = texts.to(device), labels.to(device)
            outputs = model(texts)
            loss = criterion(outputs, labels)
            val_loss += loss.item() * texts.size(0)
            val_preds.extend(outputs.argmax(1).cpu().tolist())
            val_trues.extend(labels.cpu().tolist())
    avg_val_loss = val_loss / len(val_loader.dataset)
    val_acc = accuracy_score(val_trues, val_preds)

    # — Scheduler & EarlyStopping —
    scheduler.step(val_acc)
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        torch.save(model.state_dict(), "best_cnn_text_final_test_model.pt")
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print(f"\nEarly stopping at epoch {epoch} (no val-improve for {patience} epochs).")
            break

    print(
        f"[CNN] Epoch {epoch:02d} | "
        f"Train Loss: {avg_train_loss:.4f} | "
        f"Val Loss: {avg_val_loss:.4f} | "
        f"Val Acc: {val_acc:.4f}"
    )

print(f"\n🎯 Best CNN Val Acc: {best_val_acc:.4f}")

# 5) TEST DEĞERLENDİRMESİ
# En iyi ağırlıkları yükle
best_cnn = CNNTextModel(
    vocab_size=len(stoi),
    embed_dim=EMBED_DIM,
    num_filters=100,
    filter_sizes=[3,4,5],
    hidden_size=128,
    num_classes=num_classes,
    embedding_weights=embedding_weights
).to(device)
best_cnn.load_state_dict(torch.load("best_cnn_text_final_test_model.pt", map_location=device))
best_cnn.eval()

test_preds, test_trues = [], []
test_loss = 0.0
with torch.no_grad():
    for texts, _, labels in tqdm(test_loader, desc="[CNN] Test", leave=False):
        texts, labels = texts.to(device), labels.to(device)
        outputs = best_cnn(texts)
        loss = criterion(outputs, labels)
        test_loss += loss.item() * texts.size(0)
        test_preds.extend(outputs.argmax(1).cpu().tolist())
        test_trues.extend(labels.cpu().tolist())

avg_test_loss = test_loss / len(test_loader.dataset)
test_acc = accuracy_score(test_trues, test_preds)

print(f"\n🔍 CNN Test Loss: {avg_test_loss:.4f} | Test Acc: {test_acc:.4f}")


Using device: cuda


/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "


[CNN] Train 1/10:   0%|          | 0/1850 [00:00<?, ?it/s]

[CNN] Val   1/10:   0%|          | 0/232 [00:00<?, ?it/s]

[CNN] Epoch 01 | Train Loss: 1.0386 | Val Loss: 0.8537 | Val Acc: 0.6618


...

[CNN] Train 10/10:   0%|          | 0/1850 [00:00<?, ?it/s]

[CNN] Val   10/10:   0%|          | 0/232 [00:00<?, ?it/s]

[CNN] Epoch 10 | Train Loss: 0.0983 | Val Loss: 0.9000 | Val Acc: 0.8220

🎯 Best CNN Val Acc: 0.8223


[CNN] Test:   0%|          | 0/232 [00:00<?, ?it/s]


🔍 CNN Test Loss: 0.8233 | Test Acc: 0.8201


### BERT

In [79]:
import torch
from torch.utils.data import Dataset, DataLoader, random_split
from transformers import BertTokenizerFast, AutoConfig, AutoModelForSequenceClassification, get_linear_schedule_with_warmup
from torch.optim import AdamW
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from tqdm.auto import tqdm

# 0) full_df’inde 'tweet', 'entity', 'label_idx' kolonlarının hazır olduğunu varsayıyoruz

# ——— 1) Train/Val/Test split ———
train_df, temp_df = train_test_split(
    full_df,
    test_size=0.20,
    stratify=full_df['label_idx'],
    random_state=42
)
val_df, test_df = train_test_split(
    temp_df,
    test_size=0.50,
    stratify=temp_df['label_idx'],
    random_state=42
)

# ——— 2) Dataset sınıfı ———
class BERTEnglishEntityDataset(Dataset):
    def __init__(self, df, tokenizer, max_len=128):
        self.df = df.reset_index(drop=True)
        self.tok = tokenizer
        self.max_len = max_len

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        text, ent = str(row['tweet']), str(row['entity'])
        # Entity’yi işaretle
        marked = text.replace(ent, f"[E_START] {ent} [E_END]")
        enc = self.tok(
            marked,
            padding='max_length',
            truncation=True,
            max_length=self.max_len,
            return_tensors='pt'
        )
        return {
            'input_ids':      enc['input_ids'].squeeze(0),
            'attention_mask': enc['attention_mask'].squeeze(0),
            'labels':         torch.tensor(int(row['label_idx']), dtype=torch.long)
        }

# ——— 3) Tokenizer ve DataLoader’lar ———
tokenizer = BertTokenizerFast.from_pretrained("bert-base-uncased")

train_ds = BERTEnglishEntityDataset(train_df, tokenizer, max_len=128)
val_ds   = BERTEnglishEntityDataset(val_df,   tokenizer, max_len=128)
test_ds  = BERTEnglishEntityDataset(test_df,  tokenizer, max_len=128)

train_loader = DataLoader(train_ds, batch_size=16, shuffle=True)
val_loader   = DataLoader(val_ds,   batch_size=16, shuffle=False)
test_loader  = DataLoader(test_ds,  batch_size=16, shuffle=False)

# ——— 4) Model, optimizer, scheduler ———
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

config = AutoConfig.from_pretrained("bert-base-uncased", num_labels=num_classes)
model  = AutoModelForSequenceClassification.from_pretrained(
    "bert-base-uncased", config=config
).to(device)

optimizer = AdamW(model.parameters(), lr=2e-5, weight_decay=0.01)
total_steps = len(train_loader) * 5  # 5 epoch çalışacağız
scheduler = get_linear_schedule_with_warmup(
    optimizer,
    num_warmup_steps=int(0.1 * total_steps),
    num_training_steps=total_steps
)

# ——— 5) Eğitim + EarlyStopping ———
best_val_acc, patience, counter = 0.0, 3, 0
NUM_EPOCHS = 5

for epoch in range(1, NUM_EPOCHS+1):
    # Training
    model.train()
    train_loss = 0.0
    for batch in tqdm(train_loader, desc=f"Epoch {epoch}/{NUM_EPOCHS} [Train]"):
        optimizer.zero_grad()
        batch = {k: v.to(device) for k, v in batch.items()}
        outputs = model(**batch)
        loss = outputs.loss
        loss.backward()
        optimizer.step()
        scheduler.step()
        train_loss += loss.item() * batch['input_ids'].size(0)
    avg_train_loss = train_loss / len(train_ds)

    # Validation
    model.eval()
    all_preds, all_labels = [], []
    with torch.no_grad():
        for batch in tqdm(val_loader, desc=f"Epoch {epoch}/{NUM_EPOCHS} [Val]"):
            inputs = {k: v.to(device) for k, v in batch.items() if k != 'labels'}
            labels = batch['labels'].to(device)
            logits = model(**inputs).logits
            preds = logits.argmax(dim=1).cpu().tolist()
            all_preds.extend(preds)
            all_labels.extend(labels.cpu().tolist())
    val_acc = accuracy_score(all_labels, all_preds)

    print(f"Epoch {epoch:02d} | Train Loss: {avg_train_loss:.4f} | Val Acc: {val_acc:.4f}")

    # EarlyStopping
    if val_acc > best_val_acc:
        best_val_acc = val_acc
        model.save_pretrained("best_bert_english_model")
        tokenizer.save_pretrained("best_bert_english_model")
        counter = 0
    else:
        counter += 1
        if counter >= patience:
            print(f"Early stopping at epoch {epoch}.")
            break

print(f"\n🎯 Best BERT‑EN Val Acc: {best_val_acc:.4f}")



/usr/local/lib/python3.11/dist-packages/huggingface_hub/file_download.py:943: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Epoch 1/5 [Train]:   0%|          | 0/3700 [00:00<?, ?it/s]

Epoch 1/5 [Val]:   0%|          | 0/463 [00:00<?, ?it/s]

Epoch 01 | Train Loss: 0.9202 | Val Acc: 0.7813


Epoch 2/5 [Train]:   0%|          | 0/3700 [00:00<?, ?it/s]

...

Epoch 5/5 [Train]:   0%|          | 0/3700 [00:00<?, ?it/s]

Epoch 5/5 [Val]:   0%|          | 0/463 [00:00<?, ?it/s]

Epoch 05 | Train Loss: 0.0606 | Val Acc: 0.9286

🎯 Best BERT‑EN Val Acc: 0.9286


/usr/local/lib/python3.11/dist-packages/huggingface_hub/file_download.py:943: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


OSError: best_bert_english_full_test_model is not a local folder and is not a valid model identifier listed on 'https://huggingface.co/models'
If this is a private repository, make sure to pass a token having permission to this repo with `use_auth_token` or log in with `huggingface-cli login` and pass `use_auth_token=True`.

In [80]:
from transformers import AutoModelForSequenceClassification, BertTokenizerFast
import torch
from sklearn.metrics import accuracy_score

# 1) Cihaz
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# 2) En iyi modeli ve tokenizer’ı yükle
best_model = AutoModelForSequenceClassification.from_pretrained("best_bert_english_model").to(device)
best_tokenizer = BertTokenizerFast.from_pretrained("best_bert_english_model")
best_model.eval()

# 3) Test dataset’i yeniden oluştur (tokenizer’ı best_tokenizer ile)
test_ds = BERTEnglishEntityDataset(test_df, best_tokenizer, max_len=128)
test_loader = DataLoader(test_ds, batch_size=16, shuffle=False)

# 4) Test üzerinde ölçüm
all_preds, all_labels = [], []
criterion = nn.CrossEntropyLoss()
test_loss = 0.0

with torch.no_grad():
    for batch in tqdm(test_loader, desc="BERT‑EN Test"):
        inputs = {k: v.to(device) for k, v in batch.items() if k != 'labels'}
        labels = batch['labels'].to(device)
        outputs = best_model(**inputs)
        logits = outputs.logits
        test_loss += criterion(logits, labels).item() * labels.size(0)
        preds = logits.argmax(dim=1).cpu().tolist()
        all_preds.extend(preds)
        all_labels.extend(labels.cpu().tolist())

avg_test_loss = test_loss / len(test_ds)
test_acc = accuracy_score(all_labels, all_preds)
print(f"\n🔍 BERT‑EN Test Loss: {avg_test_loss:.4f} | Test Acc: {test_acc:.4f}")


BERT‑EN Test:   0%|          | 0/463 [00:00<?, ?it/s]


🔍 BERT‑EN Test Loss: 0.2727 | Test Acc: 0.9257


In [82]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 395.9/395.9 kB 30.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 247.0/247.0 kB 23.2 MB/s eta 0:00:00


In [ ]:
models_info = [
    ("LSTM", LSTMEntityModel, "best_lstm_entity_test_final_fixed.pt", 0.5065),
    ("GRU", GRUEntityModel,   "best_gru_entity_final_test_es.pt",    0.2217),
    ("CNN+LSTM", CNNLSTMEntityModel, "best_cnnlstm_entity_final_test_optimized.pt", 0.4916),
]

In [92]:
import torch
import pandas as pd
from torch.utils.data import Dataset, DataLoader
from sklearn.metrics import classification_report
from tqdm.auto import tqdm
from transformers import AutoModelForSequenceClassification, BertTokenizerFast

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# 1) TEST DATASET & LOADER (entity‐based)
class EntityTestDataset(Dataset):
    def __init__(self, df):
        self.df = df.reset_index(drop=True)
    def __len__(self):
        return len(self.df)
    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        txt = mark_entity(row['tweet'], row['entity'])
        tok_txt = [stoi.get(t, stoi["<unk>"]) for t in tokenize(txt)]
        tok_ent = [stoi.get(t, stoi["<unk>"]) for t in tokenize(str(row['entity']))]
        lbl     = int(row['label_idx'])
        return torch.tensor(tok_txt), torch.tensor(tok_ent), torch.tensor(lbl)

def collate_entity(batch):
    texts, ents, labels = zip(*batch)
    texts_p = pad_sequence(texts, batch_first=True, padding_value=stoi["<pad>"])
    ents_p  = pad_sequence(ents,  batch_first=True, padding_value=stoi["<pad>"])
    return texts_p.long(), ents_p.long(), torch.stack(labels).long()

entity_test_loader = DataLoader(
    EntityTestDataset(test_df),
    batch_size=32,
    shuffle=False,
    collate_fn=collate_entity,
    pin_memory=True
)

# 2) TEST DATASET & LOADER (BERT)
bert_tokenizer = BertTokenizerFast.from_pretrained("best_bert_english_model")
class BERTTestDataset(Dataset):
    def __init__(self, df, tokenizer, max_len=128):
        self.df = df.reset_index(drop=True)
        self.tok = tokenizer
        self.max_len = max_len
    def __len__(self):
        return len(self.df)
    def __getitem__(self, idx):
        row = self.df.iloc[idx]
        text, ent = str(row['tweet']), str(row['entity'])
        marked = text.replace(ent, f"[E_START] {ent} [E_END]")
        enc = self.tok(marked, padding='max_length', truncation=True,
                       max_length=self.max_len, return_tensors='pt')
        return {
            'input_ids':      enc['input_ids'].squeeze(0),
            'attention_mask': enc['attention_mask'].squeeze(0),
            'labels':         torch.tensor(int(row['label_idx']), dtype=torch.long)
        }

bert_test_loader = DataLoader(
    BERTTestDataset(test_df, bert_tokenizer, max_len=128),
    batch_size=16,
    shuffle=False,
    pin_memory=True
)

# 3) Sınıf sıralaması
label_order = ["Irrelevant", "Negative", "Neutral", "Positive"]

# 4) Modellerin bilgileri
models_info = [
    {"name":"LSTM",     "type":"entity", "class":LSTMEntityModel,    "ckpt":"best_lstm_entity_test_final_fixed.pt",         "dropout":0.5065},
    {"name":"GRU",      "type":"entity", "class":GRUEntityModel,     "ckpt":"best_gru_entity_final_test_es.pt",             "dropout":0.2217},
    {"name":"CNN+LSTM","type":"entity", "class":CNNLSTMEntityModel, "ckpt":"best_cnnlstm_entity_final_test_optimized.pt", "dropout":0.4916, "extra":{"num_filters":150,"filter_size":3}},
    {"name":"CNN",      "type":"entity", "class":CNNTextModel,       "ckpt":"best_cnn_text_final_test_model.pt",            "dropout":0.5,    "extra":{"num_filters":100,"filter_sizes":[3,4,5],"hidden_size":128}},
    {"name":"BERT‑EN",  "type":"bert",   "ckpt":"best_bert_english_model"}
]

rows = []

for info in models_info:
    name = info["name"]
    # --- instantiate & load ---
    if info["type"] == "entity":
        Cls = info["class"]
        extra = info.get("extra", {})
        if name == "CNN+LSTM":
            model = Cls(len(stoi), EMBED_DIM,
                        extra["num_filters"], extra["filter_size"],
                        256, num_classes, embedding_weights)
        elif name == "CNN":
            model = Cls(len(stoi), EMBED_DIM,
                        num_filters=extra["num_filters"],
                        filter_sizes=extra["filter_sizes"],
                        hidden_size=extra["hidden_size"],
                        num_classes=num_classes,
                        embedding_weights=embedding_weights)
        else:  # LSTM or GRU
            model = Cls(len(stoi), EMBED_DIM, 256, num_classes, embedding_weights)
        model.to(device)
        model.fc[2].p = info["dropout"]
        model.load_state_dict(torch.load(info["ckpt"], map_location=device))
        model.eval()

        loader = entity_test_loader
        all_preds, all_labels = [], []
        with torch.no_grad():
            for texts, ents, labels in tqdm(loader, desc=name):
                texts, ents = texts.to(device), ents.to(device)
                out = model(texts, ents) if name!="CNN" else model(texts)
                all_preds.extend(out.argmax(1).cpu().tolist())
                all_labels.extend(labels.tolist())

    else:  # BERT‑EN
        model = AutoModelForSequenceClassification.from_pretrained(info["ckpt"]).to(device)
        model.eval()
        loader = bert_test_loader
        all_preds, all_labels = [], []
        with torch.no_grad():
            for batch in tqdm(loader, desc=name):
                inputs = {k:v.to(device) for k,v in batch.items() if k!="labels"}
                labels = batch["labels"].to(device)
                logits = model(**inputs).logits
                all_preds.extend(logits.argmax(1).cpu().tolist())
                all_labels.extend(labels.cpu().tolist())

    # --- classification report ---
    rep = classification_report(
        all_labels, all_preds,
        target_names=label_order,
        output_dict=True, zero_division=0
    )
    for cls in label_order:
        rows.append({
            "Model":    name,
            "Class":    cls,
            "Precision":rep[cls]["precision"],
            "Recall":   rep[cls]["recall"],
            "F1-Score": rep[cls]["f1-score"],
            "Support":  int(rep[cls]["support"])
        })

# 5) Pivot and display
df_metrics = pd.DataFrame(rows)
pivot = df_metrics.pivot(
    index="Class",
    columns="Model",
    values=["Precision","Recall","F1-Score","Support"]
)

print(pivot)


LSTM:   0%|          | 0/232 [00:00<?, ?it/s]

GRU:   0%|          | 0/232 [00:00<?, ?it/s]

CNN+LSTM:   0%|          | 0/232 [00:00<?, ?it/s]

CNN:   0%|          | 0/232 [00:00<?, ?it/s]

BERT‑EN:   0%|          | 0/463 [00:00<?, ?it/s]

           Precision                                            Recall  \
Model        BERT‑EN       CNN  CNN+LSTM       GRU      LSTM   BERT‑EN   
Class                                                                    
Irrelevant  0.944490  0.772053  0.827229  0.641355  0.835341  0.898990   
Negative    0.938876  0.891496  0.878926  0.669040  0.854211  0.934258   
Neutral     0.910118  0.764646  0.829653  0.700068  0.838587  0.933738   
Positive    0.914436  0.832298  0.850367  0.652553  0.878543  0.925944   

                                                    F1-Score            \
Model            CNN  CNN+LSTM       GRU      LSTM   BERT‑EN       CNN   
Class                                                                    
Irrelevant  0.768454  0.807304  0.426573  0.808081  0.921178  0.770249   
Negative    0.815742  0.863596  0.798301  0.893560  0.936561  0.851938   
Neutral     0.836002  0.871342  0.567090  0.852015  0.921777  0.798734   
Positive    0.843175  0.841723  0.760